In [13]:
// #load "NbHelper.fsx"

#I "../Vide.Common/src/Vide.Common.DSP/bin/Debug/netstandard2.0"
#r "Vide.Common.dll"
#r "Vide.Common.DSP.dll"

#r "nuget: Plotly.NET, 4.2.0"
#r "nuget: Plotly.NET.Interactive, 4.2.0"

Installed Packages Plotly.NET, 4.2.0 Plotly.NET.Interactive, 4.2.0

In [14]:
open Vide
open Vide.DSP
open Vide.DSP.Operators
open Vide.DSP.DiscreteTime

open Plotly.NET
open Plotly.NET.LayoutObjects

let plotLineXY xvalues (yvalues: _ list) =
    Chart.Line(xvalues, yvalues)
    |> Chart.withSize(800.0, 300.0)
    |> Chart.withMargin(Margin.init(5,5,15,5))

let plotLine (yvalues: _ list) =
    let xvalues = List.init (yvalues |> List.length) float
    plotLineXY xvalues yvalues 

let plotVide sampleRate durationInSeconds (gen: Vide<_,_,_>) =
    let yvalues =
        gen 
        |> Gen.Eval.toSeq sampleRate
        |> Seq.take (sampleRate * durationInSeconds |> int)
        |> Seq.toList
    let xvalues = List.init yvalues.Length (fun y -> float y / float sampleRate)
    plotLineXY xvalues yvalues
    
let plotVides sampleRate durationInSeconds gens =
    gens
    |> List.map (plotVide sampleRate durationInSeconds)
    |> Chart.combine

let plotVide44k durationInSeconds gen = plotVide 44100 durationInSeconds gen
    
let plotVides44k durationInSeconds gens = plotVides 44100 durationInSeconds gens

In [18]:
// modulate a sine wave with another sine wave
let modulatedSignal = dsp {
    let! sin1 = Gen.Osc.sin 30.0
    let! sin2 = Gen.Osc.sin 7.0
    return sin1 * sin2
}

modulatedSignal |> plotVide44k 1

<!-- Plotly chart will be drawn inside this DIV -->

In [19]:
// apply some noise to the modulates signal
let noisyModulated = dsp {
    let! modulated = modulatedSignal
    let! noise = Gen.Osc.noise
    return modulated * noise
}

noisyModulated |> plotVide44k 1

<!-- Plotly chart will be drawn inside this DIV -->

In [20]:
[
    noisyModulated |> plotVide44k 1
    (
        noisyModulated
        |=> Fx.Filter.lowPass { frq = 50.0; q = 0.9; gain = 1.0 }
        |> plotVide44k 1
    )
]
|> Chart.combine


<!-- Plotly chart will be drawn inside this DIV -->